In [1]:
#%%
import os

import datetime as dt
import pytz
import plotly.graph_objects as go
from insolAPI.WebAPI import API
import simplejson as json
import pandas as pd
import numpy as np
import matplotlib as plt
from plotly.subplots import make_subplots

# installation_path = os.path.abspath(os.path.join(os.path.dirname(__name__), '../Installations/'))
installation_path = "C:/Users/Insolight/Desktop/InsolReports/Installations/"
with open(installation_path+'/local.json') as f:
    local_data = json.load(f)

datestart = dt.datetime(2023,11,27)
datestop = dt.datetime(2023,12,1)

# datestart = dt.datetime.now() - dt.timedelta(hours = 96)
# datestop = dt.datetime.now() + dt.timedelta(hours = 2)

start_date_utc = datestart.astimezone(pytz.UTC)
stop_date_utc = datestop.astimezone(pytz.UTC)


## Global parameters

In [2]:
rain_parameters = {
    'limit' : 5,
    'critical_limit' : 15,
    'buffer_size' : 20,
    'threshold_on' : 0.5,
    'threshold_off' : 0.2,
}
wind_parameters = {
    'limit' : 4.2,
    'critical_limit' : 7.2,
    'buffer_size' : 20,
    'threshold_on' : 0.5,
    'threshold_off' : 0.2,
}


## Functions

In [3]:
def preprocess_rain(df_init, installation_params):
    df = df_init[df_init.channel_name == 'rainfall']
    df = df[df.sensor_name.isin(installation_params['rain_sensors'])]
    df = pd.pivot_table(data = df, columns = 'sensor_name', index = df.index, values=['Rain [mm/h]']).ffill()
    df = df.groupby(axis=1, level=0).mean()
    df = df.resample('1min').ffill(limit=8)
    df["rain_limit"] = (df.loc[:,"Rain [mm/h]"] >= rain_parameters['limit']).astype('int32')
    df["rain_critical_limit"] = (df.loc[:,"Rain [mm/h]"] >= rain_parameters['critical_limit']).astype('int32')
    df["rain_limit_rolling"] = df.loc[:,"rain_limit"].rolling(rain_parameters['buffer_size']).mean()
    df["ON_tmp"] = (df.loc[:,"rain_limit_rolling"]>=rain_parameters['threshold_on']).astype('int32')
    df["OFF_tmp"] = (df.loc[:,"rain_limit_rolling"]<=rain_parameters['threshold_off']).astype('int32')
    df["rain_count"] = df.loc[:,"Rain [mm/h]"].isna().rolling(wind_parameters['buffer_size']).mean()
    df["ON"] = np.nan
    df["ON"][df.loc[:,"rain_limit_rolling"]>=rain_parameters['threshold_on']] = 1
    df["ON"][df.loc[:,"rain_count"]>=wind_parameters['threshold_on']] = 1
    df["ON"][df.loc[:,"rain_limit_rolling"]<=rain_parameters['threshold_off']] = 0
    df["ON"][df["rain_critical_limit"] == 1] = 1
    df["ON"] = df["ON"].ffill()
    return df

In [4]:
def preprocess_wind(df_init, installation_params):
    df = df_init[df_init.channel_name=='wind_speed'].copy()
    df = df[df.sensor_name.isin(installation_params['wind_sensors'])]
    df = pd.pivot_table(data = df, columns = 'sensor_name', index = df.index, values=['Wind speed [m/s]']).ffill()
    df = df.groupby(axis=1, level=0).mean()
    df = df.resample('1min').ffill(limit=8)
    df["wind_limit"] = (df.loc[:,"Wind speed [m/s]"] >= wind_parameters['limit']).astype('int32')
    df["wind_critical_limit"] = (df.loc[:,"Wind speed [m/s]"] >= wind_parameters['critical_limit']).astype('int32')
    df["wind_limit_rolling"] = df.loc[:,"wind_limit"].rolling(wind_parameters['buffer_size']).mean()
    df["wind_count"] = df.loc[:,"Wind speed [m/s]"].isna().rolling(wind_parameters['buffer_size']).mean()
    df["ON"] = np.nan
    df["ON"][((df.loc[:,"wind_limit_rolling"]>=wind_parameters['threshold_on'])|(df.loc[:,"wind_count"]>=wind_parameters['threshold_on']))] = 1
    df["ON"][((df.loc[:,"wind_limit_rolling"]<=wind_parameters['threshold_off'])&(df.loc[:,"wind_count"]<=wind_parameters['threshold_off']))] = 0
    df["ON"][df["wind_critical_limit"] == 1] = 1
    df["ON"] = df["ON"].ffill()
    return df

## Download data

### Agroscope Serie

In [5]:
api, zone_id = API(local_data['API_user'], local_data['API_pwd'], dev_space=False, install=24), 1
Agroscope_serie_param = {
    'wind_sensors' : ['wind_speed','wind_speed_ultrasonic'],
    'rain_sensors' : ['weather_station'],
}

In [6]:
Sensors_data_RAIN_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.RAIN)
Sensors_data_RAIN_TYPE_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.RAIN_TYPE)
Sensors_data_WIND_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.WIND)

screen_logs_tmp = api.get_screens_logs_joined(start=start_date_utc, stop=stop_date_utc)
mot_logs_tmp = api.get_motors_logs_joined(start=start_date_utc, stop=stop_date_utc)
algo_logs_tmp = api.get_algorithms_logs_csv(start=start_date_utc, stop=stop_date_utc)
agroscope_serie_screen_logs = dict()
for id in screen_logs_tmp.zone_name.unique():
    screen_logs_1 = screen_logs_tmp[screen_logs_tmp.zone_name == id]
    screen_logs_resample = screen_logs_1.resample('5min').ffill()
    agroscope_serie_screen_logs[id] = screen_logs_resample
agroscope_serie_motor_logs = dict()
for id in mot_logs_tmp.name.unique():
    motor_logs_1 = mot_logs_tmp[mot_logs_tmp.name == id]
    motor_logs_resample = motor_logs_1.resample('5min').ffill()
    agroscope_serie_motor_logs[id] = motor_logs_resample


c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  index = pd.to_datetime(dat[time_col].values, infer_datetime_format=True, dayfirst=dayfirst)
c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  index = pd.to_datetime(dat[time_col].values, infer_datetime_format=True, dayfirst=dayfirst)
c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The

In [7]:
Agroscope_serie_WIND = preprocess_wind(Sensors_data_WIND_tmp, Agroscope_serie_param)
Agroscope_serie_RAIN = preprocess_rain(Sensors_data_RAIN_tmp, Agroscope_serie_param)

C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["ON"][((df.loc[:,"wind_limit_rolling"]>=wind_parameters['threshold_on'])|(df.loc[:,"wind_count"]>=wind_parameters['threshold_on']))] = 1
C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["ON"][((df.loc[:,"wind_limit_rolling"]<=wind_parameters['threshold_off'])&(df.loc[:,"wind_count"]<=wind_parameters['threshold_off']))] = 0
C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:14: SettingWithCopyWarning: 
A value is 

### Agroscope berries

In [8]:
api, zone_id = API(local_data['API_user'], local_data['API_pwd'], dev_space=False, install=25), 1
Agroscope_berries_param = {
    'wind_sensors' : ['WIND02_EXT'],
    # 'wind_sensors' : ['WIND01_EXT','WIND02_EXT'],
    'rain_sensors' : ['RAIN_EXT'],
}

In [9]:
Sensors_data_RAIN_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.RAIN)
Sensors_data_RAIN_TYPE_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.RAIN_TYPE)
Sensors_data_WIND_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.WIND)

screen_logs_tmp = api.get_screens_logs_joined(start=start_date_utc, stop=stop_date_utc)
mot_logs_tmp = api.get_motors_logs_joined(start=start_date_utc, stop=stop_date_utc)
algo_logs_tmp = api.get_algorithms_logs_csv(start=start_date_utc, stop=stop_date_utc)
Agroscope_berries_screen_logs = dict()
for id in screen_logs_tmp.zone_name.unique():
    screen_logs_1 = screen_logs_tmp[screen_logs_tmp.zone_name == id]
    screen_logs_resample = screen_logs_1.resample('5min').ffill()
    Agroscope_berries_screen_logs[id] = screen_logs_resample
Agroscope_berries_motor_logs = dict()
for id in mot_logs_tmp.name.unique():
    motor_logs_1 = mot_logs_tmp[mot_logs_tmp.name == id]
    motor_logs_resample = motor_logs_1.resample('5min').ffill()
    Agroscope_berries_motor_logs[id] = motor_logs_resample


c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  index = pd.to_datetime(dat[time_col].values, infer_datetime_format=True, dayfirst=dayfirst)
c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  index = pd.to_datetime(dat[time_col].values, infer_datetime_format=True, dayfirst=dayfirst)
c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The

In [10]:
Agroscope_berries_WIND = preprocess_wind(Sensors_data_WIND_tmp, Agroscope_berries_param)
Agroscope_berries_RAIN = preprocess_rain(Sensors_data_RAIN_tmp, Agroscope_berries_param)

C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["ON"][((df.loc[:,"wind_limit_rolling"]>=wind_parameters['threshold_on'])|(df.loc[:,"wind_count"]>=wind_parameters['threshold_on']))] = 1
C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["ON"][((df.loc[:,"wind_limit_rolling"]<=wind_parameters['threshold_off'])&(df.loc[:,"wind_count"]<=wind_parameters['threshold_off']))] = 0
C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:14: SettingWithCopyWarning: 
A value is 

### Bioschmid

In [11]:
api, zone_id = API(local_data['API_user'], local_data['API_pwd'], dev_space=False, install=23), 1
Bioschmid_param = {
    'wind_sensors' : ['WIND01_EXT','WIND02_EXT'],
    'rain_sensors' : ['RAIN01_EXT'],
}

In [12]:
Sensors_data_RAIN_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.RAIN)
Sensors_data_RAIN_TYPE_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.RAIN_TYPE)
Sensors_data_WIND_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.WIND)

screen_logs_tmp = api.get_screens_logs_joined(start=start_date_utc, stop=stop_date_utc)
mot_logs_tmp = api.get_motors_logs_joined(start=start_date_utc, stop=stop_date_utc)
algo_logs_tmp = api.get_algorithms_logs_csv(start=start_date_utc, stop=stop_date_utc)
bioschmid_screen_logs = dict()
for id in screen_logs_tmp.zone_name.unique():
    screen_logs_1 = screen_logs_tmp[screen_logs_tmp.zone_name == id]
    screen_logs_resample = screen_logs_1.resample('5min').ffill()
    bioschmid_screen_logs[id] = screen_logs_resample
bioschmid_motor_logs = dict()
for id in mot_logs_tmp.name.unique():
    motor_logs_1 = mot_logs_tmp[mot_logs_tmp.name == id]
    motor_logs_resample = motor_logs_1.resample('5min').ffill()
    bioschmid_motor_logs[id] = motor_logs_resample


c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  index = pd.to_datetime(dat[time_col].values, infer_datetime_format=True, dayfirst=dayfirst)
c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  index = pd.to_datetime(dat[time_col].values, infer_datetime_format=True, dayfirst=dayfirst)
c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The

In [13]:
Bioschmid_WIND = preprocess_wind(Sensors_data_WIND_tmp, Bioschmid_param)
Bioschmid_RAIN = preprocess_rain(Sensors_data_RAIN_tmp, Bioschmid_param)

C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["ON"][((df.loc[:,"wind_limit_rolling"]>=wind_parameters['threshold_on'])|(df.loc[:,"wind_count"]>=wind_parameters['threshold_on']))] = 1
C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["ON"][((df.loc[:,"wind_limit_rolling"]<=wind_parameters['threshold_off'])&(df.loc[:,"wind_count"]<=wind_parameters['threshold_off']))] = 0
C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:14: SettingWithCopyWarning: 
A value is 

### Etchelecu

In [14]:
api, zone_id = API(local_data['API_user'], local_data['API_pwd'], dev_space=False, install=26), 1
Etchelecu_param = {
    'wind_sensors' : ['WIND01_EXT','WIND02_EXT'],
    'rain_sensors' : ['RAIN_EXT'],
}

In [15]:
Sensors_data_RAIN_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.RAIN)
Sensors_data_RAIN_TYPE_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.RAIN_TYPE)
Sensors_data_WIND_tmp = api.get_sensor_channels_logs_joined(start=start_date_utc, stop=stop_date_utc,
    sensor_type=API.SensorsTypes.WIND)

screen_logs_tmp = api.get_screens_logs_joined(start=start_date_utc, stop=stop_date_utc)
mot_logs_tmp = api.get_motors_logs_joined(start=start_date_utc, stop=stop_date_utc)
algo_logs_tmp = api.get_algorithms_logs_csv(start=start_date_utc, stop=stop_date_utc)
Etchelecu_screen_logs = dict()
for id in screen_logs_tmp.zone_name.unique():
    screen_logs_1 = screen_logs_tmp[screen_logs_tmp.zone_name == id]
    screen_logs_resample = screen_logs_1.resample('5min').ffill()
    Etchelecu_screen_logs[id] = screen_logs_resample
Etchelecu_motor_logs = dict()
for id in mot_logs_tmp.name.unique():
    motor_logs_1 = mot_logs_tmp[mot_logs_tmp.name == id]
    motor_logs_resample = motor_logs_1.resample('5min').ffill()
    Etchelecu_motor_logs[id] = motor_logs_resample


c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  index = pd.to_datetime(dat[time_col].values, infer_datetime_format=True, dayfirst=dayfirst)
c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  index = pd.to_datetime(dat[time_col].values, infer_datetime_format=True, dayfirst=dayfirst)
c:\Users\Insolight\mambaforge\envs\insolinsights\Lib\site-packages\insolAPI\WebAPI.py:76: UserWarning: The

In [16]:
Etchelecu_WIND = preprocess_wind(Sensors_data_WIND_tmp, Etchelecu_param)
Etchelecu_RAIN = preprocess_rain(Sensors_data_RAIN_tmp, Etchelecu_param)

C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["ON"][((df.loc[:,"wind_limit_rolling"]>=wind_parameters['threshold_on'])|(df.loc[:,"wind_count"]>=wind_parameters['threshold_on']))] = 1
C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["ON"][((df.loc[:,"wind_limit_rolling"]<=wind_parameters['threshold_off'])&(df.loc[:,"wind_count"]<=wind_parameters['threshold_off']))] = 0
C:\Users\Insolight\AppData\Local\Temp\ipykernel_17600\2215151528.py:14: SettingWithCopyWarning: 
A value is 

## Check protection mode well activated

In [17]:
fig = make_subplots(rows=3, shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.03)

fig.add_traces([
    go.Scatter(x=Agroscope_serie_RAIN.index, y=Agroscope_serie_RAIN["Rain [mm/h]"], name='Rain'),
    go.Scatter(x=[Agroscope_serie_RAIN.index[0],Agroscope_serie_RAIN.index[-1]],
               y=[rain_parameters['limit'],rain_parameters['limit']],mode = "lines", name='rain limit'),
    go.Scatter(x=[Agroscope_serie_RAIN.index[0],Agroscope_serie_RAIN.index[-1]],
               y=[rain_parameters['critical_limit'], rain_parameters['critical_limit']],mode = "lines", name='rain critical_limit'),
    ], rows=3*[1], cols=3*[1])
fig.update_yaxes(title="Rain speed [m/s]", row = 2)

fig.add_traces([
    go.Scatter(x=Agroscope_serie_WIND.index, y=Agroscope_serie_WIND["Wind speed [m/s]"], name='Wind',mode = "lines+markers"),
    go.Scatter(x=[Agroscope_serie_WIND.index[0],Agroscope_serie_WIND.index[-1]],
               y=[wind_parameters['limit'],wind_parameters['limit']],mode = "lines", name='wind limit'),
    go.Scatter(x=[Agroscope_serie_WIND.index[0],Agroscope_serie_WIND.index[-1]],
               y=[wind_parameters['critical_limit'], wind_parameters['critical_limit']],mode = "lines", name='wind critical_limit'),
], rows=3*[2], cols=3*[1])
fig.update_yaxes(title="Wind speed [m/s]", row = 2)

fig.add_traces([
    go.Scatter(x=Agroscope_serie_RAIN.index, y=Agroscope_serie_RAIN["ON"]*6, name='Screen should retract for rain protection'),
    go.Scatter(x=Agroscope_serie_WIND.index, y=Agroscope_serie_WIND["ON"]*6, name='Screen retract for wind protection'),
], rows=2*[3], cols=2*[1])

for id, screen in agroscope_serie_screen_logs.items():
    fig.add_traces([
        go.Scatter(x=screen.index, y=screen.state, name='screen state ' + id, mode='markers+lines')
    ], rows=1*[3], cols=1*[1])

fig.update_yaxes(title="Screen modes", row = 3,tickvals = [1,2,3,4,5,6],
    ticktext = ['AUTO', 'MANUAL', 'EMERGENCY', 'PROTECTION', 'DEMO', 'REMOTE'])
fig.update_layout(width=1200, height = 700, title = 'Agroscope serie')

In [18]:
fig = make_subplots(rows=3, shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.03)

fig.add_traces([
    go.Scatter(x=Agroscope_berries_RAIN.index, y=Agroscope_berries_RAIN["Rain [mm/h]"], name='Rain'),
    go.Scatter(x=[Agroscope_berries_RAIN.index[0],Agroscope_berries_RAIN.index[-1]],
               y=[rain_parameters['limit'],rain_parameters['limit']],mode = "lines", name='rain limit'),
    go.Scatter(x=[Agroscope_berries_RAIN.index[0],Agroscope_berries_RAIN.index[-1]],
               y=[rain_parameters['critical_limit'], rain_parameters['critical_limit']],mode = "lines", name='rain critical_limit'),
    ], rows=3*[1], cols=3*[1])
fig.update_yaxes(title="Rain speed [m/s]", row = 2)

fig.add_traces([
    go.Scatter(x=Agroscope_berries_WIND.index, y=Agroscope_berries_WIND["Wind speed [m/s]"], name='Wind',mode = "lines+markers"),
    go.Scatter(x=[Agroscope_berries_WIND.index[0],Agroscope_berries_WIND.index[-1]],
               y=[wind_parameters['limit'],wind_parameters['limit']],mode = "lines", name='wind limit'),
    go.Scatter(x=[Agroscope_berries_WIND.index[0],Agroscope_berries_WIND.index[-1]],
               y=[wind_parameters['critical_limit'], wind_parameters['critical_limit']],mode = "lines", name='wind critical_limit'),
], rows=3*[2], cols=3*[1])
fig.update_yaxes(title="Wind speed [m/s]", row = 2)

fig.add_traces([
    go.Scatter(x=Agroscope_berries_RAIN.index, y=Agroscope_berries_RAIN["ON"]*6, name='Screen retract for rain protection'),
    go.Scatter(x=Agroscope_berries_WIND.index, y=Agroscope_berries_WIND["ON"]*6, name='Screen retract for wind protection'),
], rows=2*[3], cols=2*[1])

for id, screen in Agroscope_berries_screen_logs.items():
    fig.add_traces([
        go.Scatter(x=screen.index, y=screen.state, name='screen state ' + id, mode='markers+lines')
    ], rows=1*[3], cols=1*[1])

fig.update_yaxes(title="Screen modes", row = 3,tickvals = [1,2,3,4,5,6],
    ticktext = ['AUTO', 'MANUAL', 'EMERGENCY', 'PROTECTION', 'DEMO', 'REMOTE'])
fig.update_layout(width=1200, height = 700, title = 'Agroscope berries')

In [19]:
fig = make_subplots(rows=3, shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.03)

fig.add_traces([
    go.Scatter(x=Bioschmid_RAIN.index, y=Bioschmid_RAIN["Rain [mm/h]"], name='Rain'),
    go.Scatter(x=[Bioschmid_RAIN.index[0],Bioschmid_RAIN.index[-1]],
               y=[rain_parameters['limit'],rain_parameters['limit']],mode = "lines", name='rain limit'),
    go.Scatter(x=[Bioschmid_RAIN.index[0],Bioschmid_RAIN.index[-1]],
               y=[rain_parameters['critical_limit'], rain_parameters['critical_limit']],mode = "lines", name='rain critical_limit'),
    ], rows=3*[1], cols=3*[1])
fig.update_yaxes(title="Rain speed [m/s]", row = 2)

fig.add_traces([
    go.Scatter(x=Bioschmid_WIND.index, y=Bioschmid_WIND["Wind speed [m/s]"], name='Wind',mode = "lines+markers"),
    go.Scatter(x=[Bioschmid_WIND.index[0],Bioschmid_WIND.index[-1]],
               y=[wind_parameters['limit'],wind_parameters['limit']],mode = "lines", name='wind limit'),
    go.Scatter(x=[Bioschmid_WIND.index[0],Bioschmid_WIND.index[-1]],
               y=[wind_parameters['critical_limit'], wind_parameters['critical_limit']],mode = "lines", name='wind critical_limit'),
], rows=3*[2], cols=3*[1])
fig.update_yaxes(title="Wind speed [m/s]", row = 2)

fig.add_traces([
    go.Scatter(x=Bioschmid_RAIN.index, y=Bioschmid_RAIN["ON"]*6, name='Screen should retract for rain protection'),
    go.Scatter(x=Bioschmid_WIND.index, y=Bioschmid_WIND["ON"]*6, name='Screen retract for wind protection'),
], rows=2*[3], cols=2*[1])

for id, screen in bioschmid_screen_logs.items():
    fig.add_traces([
        go.Scatter(x=screen.index, y=screen.state, name='screen state ' + id, mode='markers+lines')
    ], rows=1*[3], cols=1*[1])

fig.update_yaxes(title="Screen modes", row = 3,tickvals = [1,2,3,4,5,6],
    ticktext = ['AUTO', 'MANUAL', 'EMERGENCY', 'PROTECTION', 'DEMO', 'REMOTE'])
fig.update_layout(width=1200, height = 700, title = 'Bioschmid')

In [21]:
fig = make_subplots(rows=3, shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.03)

fig.add_traces([
    go.Scatter(x=Etchelecu_RAIN.index, y=Etchelecu_RAIN["Rain [mm/h]"], name='Rain'),
    go.Scatter(x=[Etchelecu_RAIN.index[0],Etchelecu_RAIN.index[-1]],
               y=[rain_parameters['limit'],rain_parameters['limit']],mode = "lines", name='rain limit'),
    go.Scatter(x=[Etchelecu_RAIN.index[0],Etchelecu_RAIN.index[-1]],
               y=[rain_parameters['critical_limit'], rain_parameters['critical_limit']],mode = "lines", name='rain critical_limit'),
    ], rows=3*[1], cols=3*[1])
fig.update_yaxes(title="Rain speed [m/s]", row = 2)

fig.add_traces([
    go.Scatter(x=Etchelecu_WIND.index, y=Etchelecu_WIND["Wind speed [m/s]"], name='Wind',mode = "lines+markers"),
    go.Scatter(x=[Etchelecu_WIND.index[0],Etchelecu_WIND.index[-1]],
               y=[wind_parameters['limit'],wind_parameters['limit']],mode = "lines", name='wind limit'),
    go.Scatter(x=[Etchelecu_WIND.index[0],Etchelecu_WIND.index[-1]],
               y=[wind_parameters['critical_limit'], wind_parameters['critical_limit']],mode = "lines", name='wind critical_limit'),
], rows=3*[2], cols=3*[1])
fig.update_yaxes(title="Wind speed [m/s]", row = 2)

fig.add_traces([
    go.Scatter(x=Etchelecu_RAIN.index, y=Etchelecu_RAIN["ON"]*6, name='Screen should retract for rain protection'),
    go.Scatter(x=Etchelecu_WIND.index, y=Etchelecu_WIND["ON"]*6, name='Screen retract for wind protection'),
], rows=2*[3], cols=2*[1])

for id, screen in Etchelecu_screen_logs.items():
    fig.add_traces([
        go.Scatter(x=screen.index, y=screen.state, name='screen state ' + id, mode='markers+lines')
    ], rows=1*[3], cols=1*[1])

fig.update_yaxes(title="Screen modes", row = 3,tickvals = [1,2,3,4,5,6],
    ticktext = ['AUTO', 'MANUAL', 'EMERGENCY', 'PROTECTION', 'DEMO', 'REMOTE'])
fig.update_layout(width=1200, height = 700, title = 'Etchelecu')

## Check if motors go to right position

In [22]:
fig = make_subplots(rows=3, shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.03)

for id, motor in agroscope_serie_motor_logs.items():
    fig.add_traces([
        go.Scatter(x=motor.index, y=motor["position"], name=id, mode='markers+lines'),
    ], rows=1*[1], cols=1*[1])
fig.update_yaxes(title="Motors positions", row = 1)

for id, motor in agroscope_serie_motor_logs.items():
    fig.add_traces([
        go.Scatter(x=motor.index, y=motor["status"], name=id, mode='markers+lines'),
    ], rows=1*[2], cols=1*[1])
fig.update_yaxes(title="Motors status", row = 2,tickvals = [1,2,3,4,5],
    ticktext = ['STOPPED', 'STARTING', 'MOVING', 'FAULT', 'BLOCKED'])


for id, screen in agroscope_serie_screen_logs.items():
    fig.add_traces([
        go.Scatter(x=screen.index, y=screen.state, name='screen state ' + id, mode='markers+lines')
    ], rows=1*[3], cols=1*[1])
fig.update_yaxes(title="Screen modes", row = 3,tickvals = [1,2,3,4,5,6],
    ticktext = ['AUTO', 'MANUAL', 'EMERGENCY', 'PROTECTION', 'DEMO', 'REMOTE'])
fig.update_layout(width=1200, height = 600, title = 'Agroscope serie')

In [23]:
fig = make_subplots(rows=3, shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.03)

for id, motor in Agroscope_berries_motor_logs.items():
    zone = id.replace('follower_','').replace('leader_','')
    fig.add_traces([
        go.Scatter(x=motor.index, y=motor["position"], name=id, mode='markers+lines', legendgroup=zone, legendgrouptitle_text=zone),
    ], rows=1*[1], cols=1*[1])
fig.update_yaxes(title="Motors positions", row = 1)

for id, motor in Agroscope_berries_motor_logs.items():
    zone = id.replace('follower_','').replace('leader_','')
    fig.add_traces([
        go.Scatter(x=motor.index, y=motor["status"], name=id, mode='markers+lines', legendgroup=zone, legendgrouptitle_text=zone),
    ], rows=1*[2], cols=1*[1])
fig.update_yaxes(title="Motors status", row = 2,tickvals = [1,2,3,4,5],
    ticktext = ['STOPPED', 'STARTING', 'MOVING', 'FAULT', 'BLOCKED'])


for id, screen in Agroscope_berries_screen_logs.items():
    fig.add_traces([
        go.Scatter(x=screen.index, y=screen.state, name='screen state ' + id, mode='markers+lines')
    ], rows=1*[3], cols=1*[1])
fig.update_yaxes(title="Screen modes", row = 3,tickvals = [1,2,3,4,5,6],
    ticktext = ['AUTO', 'MANUAL', 'EMERGENCY', 'PROTECTION', 'DEMO', 'REMOTE'])
fig.update_layout(width=1200, height = 600, title = 'Agroscope berries')

In [24]:
fig = make_subplots(rows=3, shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.03)

for id, motor in bioschmid_motor_logs.items():
    fig.add_traces([
        go.Scatter(x=motor.index, y=motor["position"], name=id, mode='markers+lines'),
    ], rows=1*[1], cols=1*[1])
fig.update_yaxes(title="Motors positions", row = 1)

for id, motor in bioschmid_motor_logs.items():
    fig.add_traces([
        go.Scatter(x=motor.index, y=motor["status"], name=id, mode='markers+lines'),
    ], rows=1*[2], cols=1*[1])
fig.update_yaxes(title="Motors status", row = 2,tickvals = [1,2,3,4,5],
    ticktext = ['STOPPED', 'STARTING', 'MOVING', 'FAULT', 'BLOCKED'])


for id, screen in bioschmid_screen_logs.items():
    fig.add_traces([
        go.Scatter(x=screen.index, y=screen.state, name='screen state ' + id, mode='markers+lines')
    ], rows=1*[3], cols=1*[1])
fig.update_yaxes(title="Screen modes", row = 3,tickvals = [1,2,3,4,5,6],
    ticktext = ['AUTO', 'MANUAL', 'EMERGENCY', 'PROTECTION', 'DEMO', 'REMOTE'])
fig.update_layout(width=1200, height = 600, title = 'Bioschmid')

In [25]:
fig = make_subplots(rows=3, shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.03)

for id, motor in Etchelecu_motor_logs.items():
    fig.add_traces([
        go.Scatter(x=motor.index, y=motor["position"], name=id, mode='markers+lines'),
    ], rows=1*[1], cols=1*[1])
fig.update_yaxes(title="Motors positions", row = 1)

for id, motor in Etchelecu_motor_logs.items():
    fig.add_traces([
        go.Scatter(x=motor.index, y=motor["status"], name=id, mode='markers+lines'),
    ], rows=1*[2], cols=1*[1])
fig.update_yaxes(title="Motors status", row = 2,tickvals = [1,2,3,4,5],
    ticktext = ['STOPPED', 'STARTING', 'MOVING', 'FAULT', 'BLOCKED'])


for id, screen in Etchelecu_screen_logs.items():
    fig.add_traces([
        go.Scatter(x=screen.index, y=screen.state, name='screen state ' + id, mode='markers+lines')
    ], rows=1*[3], cols=1*[1])
fig.update_yaxes(title="Screen modes", row = 3,tickvals = [1,2,3,4,5,6],
    ticktext = ['AUTO', 'MANUAL', 'EMERGENCY', 'PROTECTION', 'DEMO', 'REMOTE'])
fig.update_layout(width=1200, height = 600, title = 'Etchelecu')